In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import geopandas as gp
import folium
import json
from folium import plugins
import boto3

In [2]:
s3 = boto3.client('s3')
obj = s3.get_object(Bucket='capstone1largedata', Key='US_Accidents_Dec19.csv')
data = pd.read_csv(obj['Body'])

/home/david/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3058: DtypeWarning: Columns (32,33,34,35,36,37,38,39,40,41,42,43,44) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
data.head()

ID    Source    TMC  Severity           Start_Time             End_Time  \
0  A-1  MapQuest  201.0         3  2016-02-08 05:46:00  2016-02-08 11:00:00   
1  A-2  MapQuest  201.0         2  2016-02-08 06:07:59  2016-02-08 06:37:59   
2  A-3  MapQuest  201.0         2  2016-02-08 06:49:27  2016-02-08 07:19:27   
3  A-4  MapQuest  201.0         3  2016-02-08 07:23:34  2016-02-08 07:53:34   
4  A-5  MapQuest  201.0         2  2016-02-08 07:39:07  2016-02-08 08:09:07   

   Start_Lat  Start_Lng  End_Lat  End_Lng  ...  Roundabout Station   Stop  \
0  39.865147 -84.058723      NaN      NaN  ...       False   False  False   
1  39.928059 -82.831184      NaN      NaN  ...       False   False  False   
2  39.063148 -84.032608      NaN      NaN  ...       False   False  False   
3  39.747753 -84.205582      NaN      NaN  ...       False   False  False   
4  39.627781 -84.188354      NaN      NaN  ...       False   False  False   

  Traffic_Calming Traffic_Signal Turning_Loop Sunrise_Sunset Civil_Twilight  \
0           False          False        False          Night          Night   
1           False          False        False          Night          Night   
2           False           True        False          Night          Night   
3           False          False        False          Night            Day   
4           False           True        False            Day            Day   

  Nautical_Twilight Astronomical_Twilight  
0             Night                 Night  
1             Night                   Day  
2               Day                   Day  
3               Day                   Day  
4               Day                   Day  

[5 rows x 49 columns]

In [4]:
data.columns

Index(['ID', 'Source', 'TMC', 'Severity', 'Start_Time', 'End_Time',
       'Start_Lat', 'Start_Lng', 'End_Lat', 'End_Lng', 'Distance(mi)',
       'Description', 'Number', 'Street', 'Side', 'City', 'County', 'State',
       'Zipcode', 'Country', 'Timezone', 'Airport_Code', 'Weather_Timestamp',
       'Temperature(F)', 'Wind_Chill(F)', 'Humidity(%)', 'Pressure(in)',
       'Visibility(mi)', 'Wind_Direction', 'Wind_Speed(mph)',
       'Precipitation(in)', 'Weather_Condition', 'Amenity', 'Bump', 'Crossing',
       'Give_Way', 'Junction', 'No_Exit', 'Railway', 'Roundabout', 'Station',
       'Stop', 'Traffic_Calming', 'Traffic_Signal', 'Turning_Loop',
       'Sunrise_Sunset', 'Civil_Twilight', 'Nautical_Twilight',
       'Astronomical_Twilight'],
      dtype='object')

In [5]:
data.shape

(2140203, 49)

In [6]:
with open('../data/2010_us_states.json') as f:
    usArea = json.load(f)

In [7]:
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 4)
folium.GeoJson(usArea).add_to(usMap)
# for i, row in data[:100000].iterrows():
#     folium.CircleMarker((row.Start_Lat, row.Start_Lng), radius=1, weight=2, color='red', fill_color='red', fill_opacity=.5).add_to(usMap)
# usMap

In [8]:
choro_df = data[['State', 'ID']].copy()

In [9]:
choro_df.head()

State   ID
0    OH  A-1
1    OH  A-2
2    OH  A-3
3    OH  A-4
4    OH  A-5

In [10]:
num_accidents_series = choro_df.groupby('State').count()

In [11]:
num_accidents_series.head()

ID
State        
AL      32701
AR        382
AZ      46398
CA     434160
CO      25149

In [12]:
num_accidents_state = pd.DataFrame()

In [13]:
num_accidents_state['state'] = [str(i) for i in num_accidents_series.index]

In [14]:
num_accidents_state['accidents'] = num_accidents_series.values

In [15]:
state_full = {'AL':'Alabama', 'AR':'Arkansas', 'AZ':'Arizona', 'CA':'California', 'CO':'Colorado', 'CT':'Connecticut', 'DC':'District of Columbia', 'DE':'Delaware','FL':'Florida', 'GA':'Georgia', 'IA':'Iowa', 'ID':'Idaho', 'IL':'Illinois', 'IN':'Indiana', 'KS':'Kansas', 'KY':'Kentucky', 'LA':'Louisiana', 'MA':'Massachusetts', 'MD':'Maryland', 'ME':'Maine', 'MI':'Michigan', 'MN':'Minnesota', 'MO':'Missouri', 'MS':'Mississippi', 'MT':'Montana', 'NC':'North Carolina', 'ND':'North Dakota', 'NE': 'Nebraska', 'NH':'New Hampshire', 'NJ':'New Jersey', 'NM':'New Mexico', 'NV': 'Nevada', 'NY':'New York', 'OH':'Ohio', 'OK':'Oklahoma', 'OR':'Oregon', 'PA':'Pennsylvania', 'RI':'Rhode Island', 'SC': 'South Carolina', 'SD': 'South Dakota', 'TN':'Tennessee', 'TX':'Texas', 'UT': 'Utah', 'VA':'Virginia', 'VT':'Vermont', 'WA':'Washington', 'WI':'Wisconsin', 'WV':'West Virginia', 'WY':'Wyoming'}

In [16]:
num_accidents_state.head()

state  accidents
0    AL      32701
1    AR        382
2    AZ      46398
3    CA     434160
4    CO      25149

In [17]:
state_full = {abbrev: state for abbrev, state in state_full.items()}

In [18]:
num_accidents_state['state'] = num_accidents_state['state'].map(state_full)

In [19]:
missing_states = [['Puerto Rico', 0], ['Alaska', 0], ['Hawaii', 0]]

In [20]:
missing_states = pd.DataFrame(missing_states, columns=['state','accidents'])

In [21]:
num_accidents_state = pd.concat([missing_states, num_accidents_state], ignore_index=True)

In [42]:
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 5)
folium.GeoJson(usArea).add_to(usMap)
usMap.choropleth(geo_data='../data/2010_us_states.json', data=num_accidents_state, columns=['state', 'accidents'], key_on='feature.properties.NAME', fill_color='YlGn', fill_opacity=1)
#usMap.save('../images/choro_map.html')

In [23]:
'''
Car Data:
https://www.statista.com/statistics/196010/total-number-of-registered-automobiles-in-the-us-by-state/
'''

'\nCar Data:\nhttps://www.statista.com/statistics/196010/total-number-of-registered-automobiles-in-the-us-by-state/\n'

In [24]:
cars_per_state = {'state': ['California', 'Texas', 'Florida', 'New York', 'Ohio', 'Illinois', 'Pennsylvania', 'Georgia', 'North Carolina', 'Virginia', 'Michigan', 'Washington', 'New Jersey', 'Arizona', 'Tennessee', 'Indiana', 'Massachusetts', 'Alabama', 'Missouri', 'Wisconsin', 'Minnesota', 'Maryland', 'South Carolina', 'Colorado', 'Kentucky', 'Oregon', 'Louisiana', 'Connecticut', 'Oklahoma', 'Iowa', 'Nevada', 'Kansas', 'Utah', 'Arkansas', 'Mississippi', 'Nebraska', 'New Mexico', 'Idaho', 'West Virginia', 'Hawaii', 'New Hampshire', 'Montana', 'Delaware', 'Rhode Island', 'Maine', 'South Dakota', 'North Dakota', 'Vermont', 'District of Columbia', 'Wyoming', 'Alaska'],'cars':[15065827,8248322,7966091,4712779,4603594,4477763,4424183,3557469,3393781,3267735,3023940,2964939,2754253,2391772,2285329,2248870,2182530,2161212,2102216,2087518,1976525,1922463,1830186,1798177,1721942,1488623,1389249,1306709,1296219,1242219,1073760,975171,937421,921161,825338,683020,655766,598774,560118,509492,506959,452845,433363,412255,390506,358859,240048,218302,209723,203546,183270]}

In [25]:
cars_per_state = pd.DataFrame(cars_per_state)

In [26]:
accident_rates = cars_per_state.set_index('state').join(num_accidents_state.set_index('state'))

In [27]:
accident_rates['accident_rate'] = accident_rates['accidents'] / accident_rates['cars']
accident_rates.reset_index(inplace=True)

In [43]:
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 5)
folium.GeoJson(usArea).add_to(usMap)
usMap.choropleth(geo_data='../data/2010_us_states.json', data=accident_rates, columns=['state', 'accident_rate'], key_on='feature.properties.NAME', fill_color='YlGn', fill_opacity=1)
#usMap.save('../images/choro_rates.html')

In [29]:
accident_rates.sort_values(by='accident_rate', ascending=False).head()

state     cars  accidents  accident_rate
22  South Carolina  1830186     133232       0.072797
28        Oklahoma  1296219      46143       0.035598
8   North Carolina  3393781     112182       0.033055
26       Louisiana  1389249      44309       0.031894
1            Texas  8248322     247922       0.030057

In [30]:
sc_data = data[data['State']=='SC'][['Start_Lat','Start_Lng']]

In [31]:
sc_data.head()

Start_Lat  Start_Lng
146283  34.318562 -82.663651
146290  34.202515 -82.134941
146296  34.293327 -81.545921
146299  34.204174 -82.195602
146300  33.457443 -81.894531

In [32]:
with open('../data/sc_area.json') as file:
    scArea = json.load(file)
scMap = folium.Map(location=[34, -79.94], tiles='Stamen Toner', zoom_start = 8)
folium.GeoJson(scArea).add_to(scMap)
scMap.add_child(plugins.HeatMap(data=sc_data[['Start_Lat', 'Start_Lng']].as_matrix(), radius=5, blur=2))
# scMap.save('../images/heat_sc.html')
scMap

/home/david/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:5: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  """


In [33]:
data['Weather_Condition'].fillna('', inplace=True)

In [34]:
snow = data[['Start_Lat', 'Start_Lng']][data['Weather_Condition'].str.contains('snow', case=False)].copy()
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 5)
folium.GeoJson(usArea).add_to(usMap)
usMap.add_child(plugins.HeatMap(data=snow[['Start_Lat', 'Start_Lng']].as_matrix(), radius=5, blur=2))
# usMap.save('../images/heat_snow.html')
usMap

/home/david/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  after removing the cwd from sys.path.


In [35]:
rain = data[['Start_Lat', 'Start_Lng']][data['Weather_Condition'].str.contains('rain', case=False)].copy()
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 5)
folium.GeoJson(usArea).add_to(usMap)
usMap.add_child(plugins.HeatMap(data=rain[['Start_Lat', 'Start_Lng']].as_matrix(), radius=5, blur=2))
#usMap.save('../images/heat_rain.html')

/home/david/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  after removing the cwd from sys.path.


In [36]:
fog = data[['Start_Lat', 'Start_Lng']][data['Weather_Condition'].str.contains('fog', case=False)].copy()
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 5)
folium.GeoJson(usArea).add_to(usMap)
usMap.add_child(plugins.HeatMap(data=fog[['Start_Lat', 'Start_Lng']].as_matrix(), radius=5, blur=2))
#usMap.save('../images/heat_fog.html')

/home/david/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  after removing the cwd from sys.path.


In [37]:
wind = data[['Start_Lat', 'Start_Lng']][data['Weather_Condition'].str.contains('wind', case=False)].copy()
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 5)
folium.GeoJson(usArea).add_to(usMap)
usMap.add_child(plugins.HeatMap(data=wind[['Start_Lat', 'Start_Lng']].as_matrix(), radius=5, blur=2))
#usMap.save('../images/heat_wind.html')

/home/david/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  after removing the cwd from sys.path.


In [38]:
smoke = data[['Start_Lat', 'Start_Lng']][data['Weather_Condition'].str.contains('smoke', case=False)].copy()
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 5)
folium.GeoJson(usArea).add_to(usMap)
usMap.add_child(plugins.HeatMap(data=smoke[['Start_Lat', 'Start_Lng']].as_matrix(), radius=5, blur=2))
#usMap.save('../images/heat_smoke.html')

/home/david/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  after removing the cwd from sys.path.


In [39]:
dust = data[['Start_Lat', 'Start_Lng']][data['Weather_Condition'].str.contains('dust', case=False)].copy()
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 5)
folium.GeoJson(usArea).add_to(usMap)
usMap.add_child(plugins.HeatMap(data=dust[['Start_Lat', 'Start_Lng']].as_matrix(), radius=5, blur=2))
#usMap.save('../images/heat_dust.html')

/home/david/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  after removing the cwd from sys.path.


In [40]:
freezing = data[['Start_Lat', 'Start_Lng']][data['Weather_Condition'].str.contains('freezing', case=False)].copy()
usMap = folium.Map(location=[39.5, -98.35], tiles='Stamen Toner', zoom_start = 5)
folium.GeoJson(usArea).add_to(usMap)
usMap.add_child(plugins.HeatMap(data=freezing[['Start_Lat', 'Start_Lng']].as_matrix(), radius=5, blur=2))
#usMap.save('../images/heat_freezing.html')

/home/david/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  after removing the cwd from sys.path.


In [44]:
data['Weather_Condition'].fillna('', inplace=True)